<a href="https://colab.research.google.com/github/jorgenery/ufba-mestrado/blob/main/Trabalho_IC0022.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>


# Apresentação Tabalho de IC0022

Alunos: **Jorge Nery** e **Iarley**

Data: 19/08/2024

## Introdução
Objetivo:
O objetivo deste projeto é transformar as rotas de linhas de ônibus em grafos e avaliar a similaridade entre elas. A análise focará no particionamento e na concorrência das rotas, buscando identificar padrões que possam contribuir para a otimização do planejamento e da eficiência do sistema de transporte público

In [5]:
# !pip install grakel
# !pip install geopy 

### Primeiro vamos decalar as funções que nos ajudaram no processo:

#### Libs Utilizadas e Funções de Carga e Tratamento de Dados

In [9]:
# Carregando Bibliotegas e Funções
import os
import random
import requests
import pandas as pd
import numpy as np
import csv
import math
import time
import _thread
import folium
from folium import plugins
import branca
from sklearn.metrics import pairwise_distances
import geopandas as gpd
from shapely.geometry import Point, Polygon, shape
from folium.plugins import Fullscreen
from branca.colormap import linear
import json
import numpy as np
from sklearn.cluster import KMeans
import matplotlib.pyplot as plt
from geopy.distance import great_circle
import networkx as nx
from grakel import GraphKernel
from grakel import graph_from_networkx



In [10]:
# Pega Pontos da Linha
def lista_Linha(arqPontos):
    df_iterator = pd.read_csv(arqPontos,sep=';',encoding='utf-8', chunksize=5000, dtype=str)
    dataset = pd.DataFrame()
    lista_linhas = set()
    for df in df_iterator:
        l = df['Codigo Linha'].unique()
        lista_linhas.update(l)
    return lista_linhas
# Pega Pontos da Linha
def pontosLinha(linha, arqPontos):
    """
    Pega itinerario de pontos da linha
    @param linha
    @return dataset com itinerario da linha
    """
    global cache_linha
    if (linha!=''):
        if (linha, arqPontos) in cache_linha:
            return cache_linha[linha, arqPontos]
        else:
            df_iterator = pd.read_csv(arqPontos,sep=';',encoding='utf-8', chunksize=5000, dtype=str)
            dataset = pd.DataFrame()
            for df in df_iterator:
                sdf = df[df['Codigo Linha']==linha].copy()
                dataset = pd.concat([dataset, sdf])
            df = dataset.copy()
            df[['SequenciaPonto']] = df[['SequenciaPonto']].apply(pd.to_numeric, errors='ignore')
            df[['Latitude Ponto','Longitude Ponto']] = df[['Latitude Ponto','Longitude Ponto']].apply(pd.to_numeric, errors='ignore')
            df = df.sort_values(['Codigo Linha','Sentido','SequenciaPonto'])
            cache_linha[linha, arqPontos]=df
            return cache_linha[linha, arqPontos]
    return None

def pontoslinha_to_grafo(df):
  G = nx.DiGraph()
  for _, row in df.iterrows():
    G.add_node(row['CodPonto'], pos=(row['Latitude Ponto'], row['Longitude Ponto']))
  for i, row1 in df.iterrows():
    p1 = int(row1['SequenciaPonto'])
    coord1 = (row1['Latitude Ponto'], row1['Longitude Ponto'])
    for j, row2 in df.iterrows():
        p2 = int(row2['SequenciaPonto'])
        coord2 = (row2['Latitude Ponto'], row2['Longitude Ponto'])
        if p2 == (p1+1):
            distance = great_circle(coord1, coord2).kilometers  # Calcula a distância geodésica entre dois pontos em metros
            G.add_edge(row1['CodPonto'], row2['CodPonto'], weight=distance)
  return G

def show_grafo(G):
  # Para visualizar o grafo, você pode usar o networkx ou outras bibliotecas de visualização
  import matplotlib.pyplot as plt
  # Obter posições dos nós para a visualização
  pos = nx.get_node_attributes(G, 'pos')
  # Desenhar o grafo
  nx.draw(G, pos, with_labels=True, node_size=700, node_color='lightblue', font_size=10, font_weight='bold')
  plt.show()

# Transforma RGB e Hexa
def rgb_to_hex(rgb):
    return '#%02x%02x%02x' % rgb

# Desenha Traçado da Linha
def desenha_mapa(linhas):
    m = folium.Map([-13.004996, -38.476245], zoom_start=13)
    shapefile_path = 'https://raw.githubusercontent.com/jorgenery/ufba-mestrado/main/datasets/Bairros_Salvador.json'
    # https://raw.githubusercontent.com/jorgenery/ufba-mestrado/main/datasets/Bairros_Salvador.json
    map_data = gpd.read_file(shapefile_path)
    geojson_data = map_data.to_crs(epsg='4326').__geo_interface__
    response = requests.get(shapefile_path)
    response.raise_for_status()  # Verificar se o download foi bem-sucedido
    area = response.json()

    colormap = linear.YlOrRd_09.scale(0,162)
    colormap

    style_function = lambda x: {
    "fillColor": colormap(x['properties']['OBJECTID'])
    }
    folium.GeoJson(geojson_data, style_function=style_function).add_to(m)

    random.seed(10)

    cor = ['','']
    for l1 in linhas:
        rgb = (random.randint(0,255),random.randint(0,255),random.randint(0,255))
        cor[0] = rgb_to_hex(rgb)
        # rgb = (rgb [0] + 10, rgb[1], rgb[2])
        cor[1] = rgb_to_hex(rgb)
        ida = l1[l1['Sentido']=='I']
        volta = l1[l1['Sentido']=='V']
        pontos_ida = ida[['Latitude Ponto','Longitude Ponto']].to_numpy()
        pontos_volta = volta[['Latitude Ponto','Longitude Ponto']].to_numpy()
        desenho_linha = folium.PolyLine(pontos_ida, weight=15, color=cor[1]).add_to(m)
        attr = {"fill": cor[0], "font-weight": "bold", "font-size": "24"}

        #plugins.PolyLineTextPath(
        #    desenho_linha, ".", repeat=True, offset=7, attributes=attr
        #).add_to(m)
        line_weight  = 4
        for j in range(len(pontos_ida)-1):
            coord = [pontos_ida[j],pontos_ida[j+1]]
            segment_width = (len(pontos_ida)-1) * (line_weight + 1)
            plugins.PolyLineOffset(
                coord,
                color=cor[1],
                weight=line_weight,
                opacity=1,
                offset=0,
            ).add_to(m)

        for j in range(len(pontos_volta)-1):
            coord = [pontos_volta[j],pontos_volta[j+1]]
            segment_width = (len(pontos_volta)-1) * (line_weight + 1)
            plugins.PolyLineOffset(
                coord,
                color=cor[0],
                weight=line_weight,
                opacity=1,
                offset=0,
            ).add_to(m)

        # plugins.PolyLineTextPath(desenho_linha, "Intinerario Linha 0710", offset=-5).add_to(m)

        folium.plugins.AntPath(
            locations=pontos_ida, color='green',reverse="True", dash_array=[2, 30]
        ).add_to(m)

        if (len(pontos_volta)>0):
            folium.plugins.AntPath(
                locations=pontos_volta, reverse="False", dash_array=[2, 30]
            ).add_to(m)

        m.fit_bounds(m.get_bounds())

        mc = plugins.MarkerCluster()


        for index, dados in l1.iterrows():
            cod_ponto = dados['CodPonto']
            endereco = dados['Endereço']
            linha = dados['Codigo Linha']
            html = f"""
              <b>Linha: {linha} </b><br>
              Outras Informações
              <p>Ponto: {cod_ponto} <br>
              <small>Endereço: {endereco}</small>
              </p>
            """
            iframe = branca.element.IFrame(html=html, width=200, height=150)
            popup = folium.Popup(iframe, max_width=500)
            m.add_child(folium.Marker([dados['Latitude Ponto'], dados['Longitude Ponto']],
                popup=popup,
                tooltip=dados['Codigo Linha']+" [ "+dados['Sentido']+" ] ("+str(dados['SequenciaPonto'])+")",
                icon=plugins.BeautifyIcon(
                    border_color="#00ABDC",
                    text_color="#00ABDC",
                    number=dados['SequenciaPonto'],
                    inner_icon_style="margin-top:0;",
                    )))

    return m

#### Formulas de Calculo de Distancia e Similaridade

In [11]:
# Função para calcular o número mínimo de operações (adição, remoção, substituição de nós ou arestas)
def distancia_edit(g1, g2):
    ged = nx.graph_edit_distance(g1, g2)
    return ged
# Função para calcular o similaridade Jaccard entre os conjuntos de arestas
def jaccard_similarity(g1, g2):
    edges_G1 = set(g1.edges())
    edges_G2 = set(g2.edges())
    return len(edges_G1.intersection(edges_G2)) / len(edges_G1.union(edges_G2))
# Graph kernels são técnicas mais avançadas para medir similaridade entre grafos, baseadas em transformações matemáticas dos grafos em vetores
def graph_kernel(g1, g2):
    # Converter grafos NetworkX para formato utilizado pelo GraKeL
    G1_grakel = graph_from_networkx([g1], node_labels_tag=None, edge_labels_tag=None)
    G2_grakel = graph_from_networkx([g2], node_labels_tag=None, edge_labels_tag=None)
    # Escolher um kernel, por exemplo, o Weisfeiler-Lehman kernel
    gk = GraphKernel(kernel=["weisfeiler_lehman", "subtree_wl"])
    # Calcular similaridade
    return gk.fit_transform(G1_grakel + G2_grakel)
# abordagem mede a similaridade encontrando subgrafos correspondentes entre dois grafos. NetworkX tem ferramentas para subgraph isomorphism
def subgraph_matching(g1, g2):
    return nx.algorithms.isomorphism.GraphMatcher(g1, g2).subgraph_is_isomorphic()

def distancia(g1, g2):
    for areta_g1 in g1:
        for aresta_g2 in g2:
            print(g1)

In [12]:
grafos

NameError: name 'grafos' is not defined

#### Criando Matriz de **Similaridade**

In [166]:
def matriz_similaridade(lista_grafos, medida_de_distancia='subgraph_matching'):
    g = list(grafos.items())
    n = len(lista_grafos)
    similaridade_matrix = np.zeros((n, n))
    for l1 in range(n):
        for l2 in range(n):
            if medida_de_distancia == 'jaccard':
              sim = jaccard_similarity(g[l1][1], g[l2][1])
            elif medida_de_distancia == 'graph_kernel':
              sim = graph_kernel(g[l1][1], g[l2][1])
            elif medida_de_distancia == 'subgraph_matching':
              sim = subgraph_matching(g[l1][1], g[l2][1])
            elif medida_de_distancia == 'distancia_edit':
              sim = distancia_edit(g[l1][1], g[l2][1])
            similaridade_matrix[l1, l2] = sim
            similaridade_matrix[l2, l1] = sim  # Matriz simétrica
    return similaridade_matrix

#### Determinando Numero de Clusters

In [167]:
# Função para determinar o número ideal de clusters usando o método do cotovelo
def elbow_method_similarity(lista_grafos, max_clusters=10, similarity_metrics=None):
    """
    Determina o número ideal de clusters usando o método do cotovelo para várias funções de similaridade.

    Parâmetros:
    - X: matriz de características ou matriz de distâncias/similaridades.
    - max_clusters: número máximo de clusters a ser avaliado.
    - similarity_metrics: lista de funções de similaridade a serem usadas. Cada função deve retornar uma matriz de similaridade.

    Retorna:
    - Um dicionário contendo a inércia para cada métrica e número de clusters.
    """
    if similarity_metrics is None:
        similarity_metrics = ['subgraph_matching']

    inertia_results = {}

    for metric in similarity_metrics:
        inertia = []
        X_sim = matriz_similaridade(lista_grafos, medida_de_distancia=metric)
        for k in range(1, max_clusters + 1):
            kmeans = KMeans(n_clusters=k)
            kmeans.fit(X_sim)
            inertia.append(kmeans.inertia_)

        inertia_results[metric if isinstance(metric, str) else metric.__name__] = inertia

    # Plotar o gráfico do cotovelo para cada métrica
    plt.figure(figsize=(10, 6))

    for metric, inertia in inertia_results.items():
        plt.plot(range(1, max_clusters + 1), inertia, marker='o', label=metric)

    plt.title('Método do Cotovelo para Diferentes Métricas de Similaridade')
    plt.xlabel('Número de Clusters')
    plt.ylabel('Inércia')
    plt.legend()
    plt.grid(True)
    plt.show()

    return inertia_results


## Contexto

In [178]:
# Carregando dados para Analise
cache_ponto = dict()
cache_linha = dict()
linhas = lista_Linha('https://raw.githubusercontent.com/jorgenery/ufba-mestrado/main/datasets/PONTOS_GPS_20191112.CSV')
df = pd.DataFrame()
grafos = {}
i = 0
for l in linhas:
  df_pontos_linha = pontosLinha(l,'https://raw.githubusercontent.com/jorgenery/ufba-mestrado/main/datasets/PONTOS_GPS_20191112.CSV')
  grafo_pontos_linha = pontoslinha_to_grafo(df_pontos_linha)
  grafos[l] = grafo_pontos_linha
  if df.empty:
    df = df_pontos_linha
  else:
    df = pd.concat([df, df_pontos_linha])
  i = i + 1
  if i > 10:
    break
df.head()

Codigo Operadora Data Operação Codigo Linha  SequenciaPonto Sentido  \
83009               26    12/11/2019         0403               1       I   
83010               26    12/11/2019         0403               2       I   
83011               26    12/11/2019         0403               3       I   
83012               26    12/11/2019         0403               4       I   
82995               26    12/11/2019         0403               5       I   

       Longitude Ponto  Latitude Ponto CodPonto  \
83009       -38.511431      -12.982944       58   
83010       -38.511083      -12.986440     3465   
83011       -38.511331      -12.990099     3466   
83012       -38.504741      -12.985458     3481   
82995       -38.503743      -12.983754     3482   

                                                Endereço  
83009  Av. Valê do Tororó, 80 - Barris, Salvador - BA...  
83010  Av. Valê do Tororó, 302-474 - Tororo, Salvador...  
83011  Avenida Centenário, 1-249 - Garcia, Salvador -...  
83012  Avenida Vasco da Gama, 245-253 - Engenho Velho...  
82995  Ladeira de Nanã, 208 - Engenho Velho de Brotas...

In [179]:
grafos

{'0403': <networkx.classes.digraph.DiGraph at 0x79c759abe260>,
 '1368': <networkx.classes.digraph.DiGraph at 0x79c768071720>,
 '1440': <networkx.classes.digraph.DiGraph at 0x79c7643d6680>,
 '0710': <networkx.classes.digraph.DiGraph at 0x79c7643d6620>,
 'R008': <networkx.classes.digraph.DiGraph at 0x79c7648cb070>,
 '0914': <networkx.classes.digraph.DiGraph at 0x79c766e351e0>,
 '032101': <networkx.classes.digraph.DiGraph at 0x79c766e12890>,
 '1225': <networkx.classes.digraph.DiGraph at 0x79c766e12980>,
 '1394': <networkx.classes.digraph.DiGraph at 0x79c766e330a0>,
 '1042': <networkx.classes.digraph.DiGraph at 0x79c7648cab30>,
 'L602': <networkx.classes.digraph.DiGraph at 0x79c76476d540>}

In [180]:
m = desenha_mapa([df['0403']])
m

## Metodologia

In [ ]:
# Calcular a matriz de distância
distance_matrix = matriz_similaridade(grafos, medida_de_distancia='subgraph_matching')
# Determinar o número ideal de clusters
elbow_method_similarity(grafos, max_clusters=1, similarity_metrics=['subgraph_matching'])

In [ ]:
# Aplicar K-means para agrupar as coordenadas
optimal_k = 3  # Suponha que escolhemos 3 clusters com base no método do cotovelo
kmeans = KMeans(n_clusters=optimal_k)
labels = kmeans.fit_predict(distance_matrix)

# Exibir os resultados
for i, label in enumerate(labels):
    print(f"Coordenada {coords[i]} está no grupo {label}")


## Resultados

## Conclusão